# Trabajo Práctico N°3: Regularización aplicada a la EPH
Federico Di Carlo y Agustin Musso

Importamos las librerías y los comandos que utilizaremos para el desarrollo de las consignas.

In [1]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from scipy.special import expit
from sklearn import svm, tree
from sklearn.base import BaseEstimator
from sklearn.model_selection import GridSearchCV, KFold, train_test_split
import warnings
warnings.filterwarnings('ignore')
# imports the models
from sklearn.ensemble import (AdaBoostClassifier, BaggingClassifier,
                              RandomForestClassifier)
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.svm import LinearSVC
# imports the metrics
from sklearn.metrics import (RocCurveDisplay, accuracy_score, confusion_matrix,
                             mean_squared_error, plot_roc_curve, roc_auc_score,
                             roc_curve)

# imports the metrics
from time import sleep
from tqdm.notebook import tqdm

## Parte I: Análisis de la base de hogares y cálculo de pobreza

Ahora que ya se han familiarizado con la Encuesta Permanente de Hogares (EPH) y con el uso de la tabla de adulto equivalente vamos a complejizar un poco la construcción del indice de pobreza. Lo calcularemos a nivel de hogares, con sus respectivos factores de expansión y realizaremos una limpieza de la base con mayor dedicación. A continuación complementaremos el trabajo hecho en el TP2 usando la encuesta a nivel de hogares de la EPH: 

1. Exploren el diseño de registro de la base de hogar: a priori, ¿qué variables creen que pueden ser muy predictivas de pobreza y que sería muy útil incluir para perfeccionar el ejercicio del TP2? 

Las características habitacionales del hogar así como las de la vivienda podrían ser predictivas de pobreza, aunque hasta cierto punto. Dado que la pobreza se calcula a través del ingreso y este puede cambiar en el tiempo, ciertas características de las viviendas que son difíciles de revertir (acceso al agua por cañería en vez de pozo, la presencia de inodoro o el tipo de desagüe) podrían haberse modificado en momentos de bonanza y luego no reflejar los cambios en la medición de pobreza que responden a factores coyunturales o macroeconómicos presentes en el trimestre. En consecuencia, podría ser deseable observar V4 y V5 (si alguien en el hogar posee seguro de desempleo o subsidio) o V6 (si el hogar recibe mercadería de alguna organziación). A su vez, V19_A (trabajo de menores del hogar) puede reflejar mejor la situación del hogar en dicho momento del tiempo que las características de la vivienda.

2. Descarguen la base de microdatos de la EPH correspondiente al primer trimestre de 2021 (la base de hogares se llama `usu_hogar_T121.xls`). Importen los datos de la encuesta de hogar y al igual que en el TP1 conserven sólo las observaciones que corresponden a los aglomerados de Ciudad Autónoma de Buenos Aires o del Gran Buenos Aires 

In [2]:
base_hogar = pd.read_excel('C:/Users/Federico/Documents/GitHub/TP3/usu_hogar_T121.xlsx')
base_hogar

CODUSU  ANO4  TRIMESTRE  NRO_HOGAR  REALIZADA  \
0      TQRMNOQUPHMKKUCDEOJAH00701956  2021          1          1          1   
1      TQRMNOPWXHMOKRCDEGLDF00701361  2021          1          1          1   
2      TQRMNOSUXHMMLPCDEGPDJ00701412  2021          1          1          1   
3      TQRMNORRQHKMKPCDEFOCD00653036  2021          1          1          1   
4      TQRMNOPYYHMKKRCDEHIBB00699594  2021          1          1          1   
...                              ...   ...        ...        ...        ...   
15418  TQRMNOSRSHJLKNCDEHNHB00686513  2021          1         72          1   
15419  TQRMNOPUPHMOKRCDEHNHB00698996  2021          1         51          1   
15420  TQRMNOPPTHKKKRCDEHPJB00655306  2021          1         71          1   
15421  TQRMNOSTVHLKSQCDEIJAH00651298  2021          1         51          1   
15422  TQRMNOPVYHKMLQCDEGGFB00653370  2021          1         51          1   

       REGION MAS_500  AGLOMERADO  PONDERA  IV1  ...  GDECCFR  PDECCFR  \
0          44       N          93       77    1  ...      NaN     12.0   
1          41       N          15      140    1  ...      NaN      6.0   
2          40       N          19      177    1  ...      NaN      7.0   
3          41       N           8      136    1  ...      NaN      2.0   
4          40       N          22      175    1  ...      NaN      7.0   
...       ...     ...         ...      ...  ...  ...      ...      ...   
15418      42       N          27      496    1  ...      9.0      NaN   
15419      42       N          27      238    1  ...      8.0      NaN   
15420      40       S          29      527    1  ...      7.0      NaN   
15421       1       S          33     1673    1  ...      8.0      NaN   
15422      42       S          10      431    1  ...     12.0      NaN   

       ADECCFR  PONDIH  VII1_1  VII1_2  VII2_1  VII2_2  VII2_3  VII2_4  
0         12.0       0      96       0      98       0       0       0  
1          8.0     191       2       0       3       5       6       0  
2          8.0     177       3       0       4       6       0       0  
3          3.0     132       2       0       3       0       0       0  
4          8.0     205       1       2       3       0       0       0  
...        ...     ...     ...     ...     ...     ...     ...     ...  
15418     10.0     497       1       0      98       0       0       0  
15419      9.0     240      97       0      98       0       0       0  
15420      8.0     664       1       0      98       0       0       0  
15421      8.0    2016       1       0      98       0       0       0  
15422     12.0       0       1       0      98       0       0       0  

[15423 rows x 88 columns]

Aqui deshacemos las observaciones que no pertenecen a los aglomerados de la Ciudad de Buenos Aires o de la Provincia de Buenos Aires

In [3]:
base_hogar.drop(base_hogar[base_hogar['AGLOMERADO'] < 32.0].index, inplace=True)
base_hogar.drop(base_hogar[base_hogar['AGLOMERADO'] > 33.0].index, inplace=True)
print(base_hogar)

                              CODUSU  ANO4  TRIMESTRE  NRO_HOGAR  REALIZADA  \
15     TQRMNOQXUHJMMUCDEIJAH00693031  2021          1          1          1   
21     TQRMNOSRPHLLNRCDEIJAH00651171  2021          1          1          1   
24     TQRMNOPVUHKLMNCDEIIAD00655817  2021          1          1          1   
36     TQRMNORYTHLOPMCDEIJAH00655933  2021          1          1          1   
43     TQRMNOQPVHLMNNCDEIIAD00650542  2021          1          1          1   
...                              ...   ...        ...        ...        ...   
15373  TQRMNOQYSHMOLTCDEIJAH00700276  2021          1          1          1   
15382  TQRMNOURVHMNONCDEIIAD00700616  2021          1          1          1   
15391  TQRMNORRWHJMOPCDEIIAD00690119  2021          1          1          1   
15412  TQRMNOQWRHLOMPCDEIJAH00650932  2021          1          1          1   
15421  TQRMNOSTVHLKSQCDEIJAH00651298  2021          1         51          1   

       REGION MAS_500  AGLOMERADO  PONDERA  IV1  ..

In [4]:
base_individuos = pd.read_excel('C:/Users/Federico/Desktop/UdeSA/Maestría/Big Data/TP3/usu_individual_T121.xlsx')
base_individuos.drop(base_individuos[base_individuos['AGLOMERADO'] < 32.0].index, inplace=True)
base_individuos.drop(base_individuos[base_individuos['AGLOMERADO'] > 33.0].index, inplace=True)
print(base_individuos)

                              CODUSU  ANO4  TRIMESTRE  NRO_HOGAR  COMPONENTE  \
36799  TQRMNOPPRHKMLNCDEIIAD00655703  2021          1          1           1   
36800  TQRMNOPPRHKMLNCDEIIAD00655703  2021          1          1           2   
36801  TQRMNOPPWHKMNUCDEIIAD00655837  2021          1          1           1   
36802  TQRMNOPPWHKMNUCDEIIAD00655837  2021          1          1           2   
36803  TQRMNOPPWHKMNUCDEIIAD00655837  2021          1          1           3   
...                              ...   ...        ...        ...         ...   
40876  TQUMNOQWTHLOTOCDEIJAH00698524  2021          1          1           2   
40877  TQUMNORVRHMMLLCDEIJAH00698180  2021          1          1           1   
40878  TQUMNORVRHMMLLCDEIJAH00698180  2021          1          1           2   
40879  TQUMNORVRHMMLLCDEIJAH00698180  2021          1          1           3   
40880  TQVMNOPYPHLOTOCDEIJAH00693364  2021          1          2           1   

       H15  REGION MAS_500  AGLOMERADO 

3. Unan la tabla de la encuesta individual con la de la encuesta de hogar.

In [5]:
import pandas as pd
base_merge= pd.merge(base_hogar, base_individuos,
                     on = "CODUSU",how = "inner")

pd.set_option('display.max_columns', None) 
display(base_merge)

CODUSU  ANO4_x  TRIMESTRE_x  NRO_HOGAR_x  \
0     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
1     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
2     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
3     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
4     TQRMNOSRPHLLNRCDEIJAH00651171    2021            1            1   
...                             ...     ...          ...          ...   
4086  TQRMNOURVHMNONCDEIIAD00700616    2021            1            1   
4087  TQRMNORRWHJMOPCDEIIAD00690119    2021            1            1   
4088  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4089  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4090  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   

      REALIZADA  REGION_x MAS_500_x  AGLOMERADO_x  PONDERA_x  IV1  IV1_ESP  \
0             1         1         S            33       3255    1      NaN   
1             1         1         S            33       3255    1      NaN   
2             1         1         S            33       3255    1      NaN   
3             1         1         S            33       3255    1      NaN   
4             1         1         S            33       2331    1      NaN   
...         ...       ...       ...           ...        ...  ...      ...   
4086          1         1         S            32       3772    2      NaN   
4087          1         1         S            32       1379    2      NaN   
4088          1         1         S            33       8638    1      NaN   
4089          1         1         S            33       8638    1      NaN   
4090          1         1         S            33       8638    1      NaN   

      IV2  IV3  IV3_ESP  IV4  IV5  IV6  IV7  IV7_ESP  IV8  IV9  IV10  IV11  \
0       9    1      NaN    2    1    1    2      NaN    1    1     1     2   
1       9    1      NaN    2    1    1    2      NaN    1    1     1     2   
2       9    1      NaN    2    1    1    2      NaN    1    1     1     2   
3       9    1      NaN    2    1    1    2      NaN    1    1     1     2   
4       9    1      NaN    3    1    1    1      NaN    1    1     1     1   
...   ...  ...      ...  ...  ...  ...  ...      ...  ...  ...   ...   ...   
4086    1    1      NaN    9    1    1    1      NaN    1    1     1     1   
4087    1    1      NaN    4    1    1    1      NaN    1    1     1     1   
4088    1    2      NaN    4    2    2    1      NaN    2    0     0     0   
4089    1    2      NaN    4    2    2    1      NaN    2    0     0     0   
4090    1    2      NaN    4    2    2    1      NaN    2    0     0     0   

      IV12_1  IV12_2  IV12_3  II1  II2  II3  II3_1  II4_1  II4_2  II4_3  II5  \
0          2       2       2    9    3    1      1      1      1      1    2   
1          2       2       2    9    3    1      1      1      1      1    2   
2          2       2       2    9    3    1      1      1      1      1    2   
3          2       2       2    9    3    1      1      1      1      1    2   
4          2       2       2    9    3    2      0      1      1      1    2   
...      ...     ...     ...  ...  ...  ...    ...    ...    ...    ...  ...   
4086       2       2       2    1    1    2      0      2      2      2    0   
4087       2       2       2    1    1    2      0      2      2      2    0   
4088       2       2       2    1    1    2      0      2      2      2    0   
4089       2       2       2    1    1    2      0      2      2      2    0   
4090       2       2       2    1    1    2      0      2      2      2    0   

      II5_1  II6  II6_1  II7  II7_ESP  II8  II8_ESP  II9  V1  V2  V21  V22  \
0         0    2      0    1      NaN    1      NaN    1   1   2    2    2   
1         0    2      0    1      NaN    1      NaN    1   1   2    2    2   
2         0    2      0    1      NaN    1      NaN    1   1   2    2    2   
3    

4. Generen sus propias funciones para limpiar la base de datos o, si deciden utilizar funciones existentes en paquetes como numpy y pandas, mencionen cuáles usarán y de qué paquetes son. Punto I.4 y Punto I.5
Para limpiar la base de datos, se tomaron dos decisiones. La primera fue borrar los duplicados generados por la unión de las bases de datos, con esto evitamos repeticiones que puedan ser nocivas para generar predicciones. La otra decisión fue eliminar las variables donde haya faltantes de datos o NaN. Esto se realizo luego de analizar la base de datos.

In [6]:
base_merge.drop(['IV1_ESP', 'IV3_ESP', 'IV7_ESP'], axis="columns", inplace=True)
base_merge.drop(['II7_ESP', 'II8_ESP', 'IDECIFR_x', 'PDECIFR_x','IDECCFR_x','PDECCFR_x','CH15_COD'], axis="columns", inplace=True)
base_merge.drop(['CH16_COD', 'IMPUTA', 'PP09C_ESP','PP09A_ESP','PP10A','PP10C','PP10D','PP10E'], axis="columns", inplace=True)
base_merge.drop(['PP11A', 'PP11B_COD', 'PP11B1','PP11B2_MES','PP11B2_ANO','PP11B2_DIA','PP11C','PP11C99','PP11D_COD'], axis="columns", inplace=True)
base_merge.drop(['PP11G_ANO', 'PP11G_MES', 'PP11G_DIA','PP11L','PP11M','PP11N','PP11O','PP11Q','PP11P','PP11Q','PP11R','PP11S','PP11T'], axis="columns", inplace=True)
base_merge.drop(['PP03C', 'PP03D', 'PP3E_TOT','PP03G','PP03H','PP03I','PP03J','INTENSI','PP04A','PP04B_COD'], axis="columns", inplace=True)
base_merge.drop(['PP04B1', 'PP04B2', 'PP04B3_MES','PP04B3_ANO','PP04B3_DIA','PP04C','PP04C99','PP04D_COD','PP04G','PP05B2_MES'], axis="columns", inplace=True)
base_merge.drop(['PP05B2_ANO', 'PP05B2_DIA', 'PP05C_1','PP05C_3','PP05E','PP05F','PP05H','PP06A','PP06D','PP06E'], axis="columns", inplace=True)
base_merge.drop(['PP06H', 'PP07A', 'PP07C','PP07D','PP07E','PP07F1','PP07F2','PP07F3','PP07F4','PP07G1'], axis="columns", inplace=True)
base_merge.drop(['PP3F_TOT', 'PP05C_2', 'PP06C','PP07F5','PP07G2','PP07G3','PP07G4','PP07G_59','PP07H','PP07I'], axis="columns", inplace=True)
base_merge.drop(['PP07J', 'PP07K', 'PP08D1','PP08F1','PP08F2','PP08J1','PP08J2','PP08J3','PP09A','PP09B','PP09C'], axis="columns", inplace=True)
base_merge.drop(['PP11L1', 'IDECOCUR', 'PDECOCUR','IDECINDR','PDECINDR'], axis="columns", inplace=True)
base_merge

CODUSU  ANO4_x  TRIMESTRE_x  NRO_HOGAR_x  \
0     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
1     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
2     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
3     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
4     TQRMNOSRPHLLNRCDEIJAH00651171    2021            1            1   
...                             ...     ...          ...          ...   
4086  TQRMNOURVHMNONCDEIIAD00700616    2021            1            1   
4087  TQRMNORRWHJMOPCDEIIAD00690119    2021            1            1   
4088  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4089  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4090  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   

      REALIZADA  REGION_x MAS_500_x  AGLOMERADO_x  PONDERA_x  IV1  IV2  IV3  \
0             1         1         S            33       3255    1    9    1   
1             1         1         S            33       3255    1    9    1   
2             1         1         S            33       3255    1    9    1   
3             1         1         S            33       3255    1    9    1   
4             1         1         S            33       2331    1    9    1   
...         ...       ...       ...           ...        ...  ...  ...  ...   
4086          1         1         S            32       3772    2    1    1   
4087          1         1         S            32       1379    2    1    1   
4088          1         1         S            33       8638    1    1    2   
4089          1         1         S            33       8638    1    1    2   
4090          1         1         S            33       8638    1    1    2   

      IV4  IV5  IV6  IV7  IV8  IV9  IV10  IV11  IV12_1  IV12_2  IV12_3  II1  \
0       2    1    1    2    1    1     1     2       2       2       2    9   
1       2    1    1    2    1    1     1     2       2       2       2    9   
2       2    1    1    2    1    1     1     2       2       2       2    9   
3       2    1    1    2    1    1     1     2       2       2       2    9   
4       3    1    1    1    1    1     1     1       2       2       2    9   
...   ...  ...  ...  ...  ...  ...   ...   ...     ...     ...     ...  ...   
4086    9    1    1    1    1    1     1     1       2       2       2    1   
4087    4    1    1    1    1    1     1     1       2       2       2    1   
4088    4    2    2    1    2    0     0     0       2       2       2    1   
4089    4    2    2    1    2    0     0     0       2       2       2    1   
4090    4    2    2    1    2    0     0     0       2       2       2    1   

      II2  II3  II3_1  II4_1  II4_2  II4_3  II5  II5_1  II6  II6_1  II7  II8  \
0       3    1      1      1      1      1    2      0    2      0    1    1   
1       3    1      1      1      1      1    2      0    2      0    1    1   
2       3    1      1      1      1      1    2      0    2      0    1    1   
3       3    1      1      1      1      1    2      0    2      0    1    1   
4       3    2      0      1      1      1    2      0    2      0    1    2   
...   ...  ...    ...    ...    ...    ...  ...    ...  ...    ...  ...  ...   
4086    1    2      0      2      2      2    0      0    0      0    3    1   
4087    1    2      0      2      2      2    0      0    0      0    3    1   
4088    1    2      0      2      2      2    0      0    0      0    2    2   
4089    1    2      0      2      2      2    0      0    0      0    2    2   
4090    1    2      0      2      2      2    0      0    0      0    2    2   

      II9  V1  V2  V21  V22  V3  V4  V5  V6  V7  V8  V9  V10  V11  V12  V13  \
0       1   1   2    2    2   2   2   2   2   2   2   2    2    2    2    2   
1       1   1   2    2    2   2   2   2   2   2   2   2    2    2    2    2   
2       1   1   2    2    2   2   2   2   2   2   2   2 

6. Presenten estadísticas descriptivas de 5 variables de la encuesta de hogar que ustedes creen que pueden ser relevantes para predecir pobreza.

In [7]:
descriptivas = base_merge[['IV1','IV6','IV8','V5','ITF_y','IPCF_y']].copy()
descriptivas.describe(include='all')

IV1         IV6          IV8           V5          ITF_y  \
count  4091.000000  4091.00000  4091.000000  4091.000000    4091.000000   
mean      1.311171     1.01320     1.001711     1.854070   54525.938890   
std       0.489219     0.11835     0.041335     0.609196   77080.708389   
min       1.000000     1.00000     1.000000     1.000000       0.000000   
25%       1.000000     1.00000     1.000000     2.000000       0.000000   
50%       1.000000     1.00000     1.000000     2.000000   32200.000000   
75%       2.000000     1.00000     1.000000     2.000000   77000.000000   
max       4.000000     3.00000     2.000000     9.000000  750000.000000   

              IPCF_y  
count    4091.000000  
mean    18794.249553  
std     28333.916280  
min         0.000000  
25%         0.000000  
50%     10000.000000  
75%     26250.000000  
max    307500.000000

7. Repitan el inciso 1.2.f del TP2 para construir la columna `adulto_equiv` y la columna `ad_equiv_hogar` (pueden utilizar su código del TP2).

In [8]:
#Se limpió el excel de comentarios, para dejar solamente la base de datos.
rp=pd.read_excel('C:/Users/Federico/Desktop/UdeSA/Maestría/Big Data/TP3/tabla_adulto_equiv.xlsx')
rp

pattern = {" a ":'-',"Menor de 1 año": "-1", "[a-zA-ZÀ-ÿ\u00f1\u00d1]":'', " ": ""}

#Limpio las edades de letras y defino menor a 1 como -1

rp['Edad'].replace(pattern, regex=True, inplace= True)

#Busco la edad maxima en la EPH y completo el rango

max_age = base_merge["CH06"].max()
rp["Edad"] = rp["Edad"].apply(lambda x: f"76-{max_age}" if x=="75" else x)

#Expando los intervalos (código conseguido de:
#https://stackoverflow.com/questions/33290362/expand-pandas-dataframe-based-on-range-in-a-column)

edades_malas = rp.loc[18:]
edades_buenas = pd.DataFrame(columns=('Edad', 'Mujeres', 'Varones'))
count = 0
for idx,r in edades_malas.iterrows():
    data = r['Edad'].split("-")
    for i in range(int(data[0]), int(data[1])+1):
                   edades_buenas.loc[count] = (i, r['Mujeres'], r['Varones'])
                   count += 1
# Junto todo en un solo df

rp = pd.concat([rp.loc[:17], edades_buenas],ignore_index=True)

# Tiro un melt para juntar hombres y mujeres en la misma columna con key 
# Mujeres = 2, Varones = 1

aequiv_for_merge = pd.melt(rp, id_vars=['Edad'], value_vars=['Mujeres', 'Varones'],
                           var_name="Genero", value_name="Adulto_equiv")
aequiv_for_merge.replace({"Mujeres": 2,"Varones": 1}, regex=True, inplace= True)
aequiv_for_merge["Edad"] = aequiv_for_merge["Edad"].apply(pd.to_numeric, errors='coerce')

# Hacemos el merge con el dataframe original. Nota: CH04 = Genero y CH06=Edad

base_merge = pd.merge(base_merge, aequiv_for_merge,  how='left', left_on=['CH04','CH06'], right_on = ['Genero','Edad'])
base_merge = base_merge.drop(columns=['Edad', 'Genero'])

In [9]:
base_merge_ad_equiv_hogar=base_merge.groupby(by=["CODUSU","NRO_HOGAR_x"],
                      as_index=False).agg(ad_equiv_hogar=('Adulto_equiv',sum))
base_merge = pd.merge(base_merge, base_merge_ad_equiv_hogar,
                      how='left', left_on=['CODUSU','NRO_HOGAR_x'], right_on = ['CODUSU','NRO_HOGAR_x'])

8. Repitan el inciso 1.3 y 1.4 del TP2 para dividir la base en dos dataframes donde: uno conserve las personas que reportaron ITF (llamada respondieron) y la otra conserve las personas que no reportaron ITF (llamada norespondieron). Además, agreguen a la base respondieron una columna llamada ingreso_necesario que sea el producto de la canasta básica por `ad_equiv_hogar`. 

Dividimos la base en dos dataframes distintos, en base a si respondieron o no lo hicieron y agregamos el ingreso necesario.

In [10]:
respondieron=base_merge[base_merge["ITF_x"] > 0]
norespondieron=base_merge[base_merge["ITF_x"] == 0]

In [11]:
respondieron["ingreso_necesario"] = respondieron["ad_equiv_hogar"]*18914
respondieron

CODUSU  ANO4_x  TRIMESTRE_x  NRO_HOGAR_x  \
0     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
1     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
2     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
3     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
4     TQRMNOSRPHLLNRCDEIJAH00651171    2021            1            1   
...                             ...     ...          ...          ...   
4086  TQRMNOURVHMNONCDEIIAD00700616    2021            1            1   
4087  TQRMNORRWHJMOPCDEIIAD00690119    2021            1            1   
4088  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4089  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4090  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   

      REALIZADA  REGION_x MAS_500_x  AGLOMERADO_x  PONDERA_x  IV1  IV2  IV3  \
0             1         1         S            33       3255    1    9    1   
1             1         1         S            33       3255    1    9    1   
2             1         1         S            33       3255    1    9    1   
3             1         1         S            33       3255    1    9    1   
4             1         1         S            33       2331    1    9    1   
...         ...       ...       ...           ...        ...  ...  ...  ...   
4086          1         1         S            32       3772    2    1    1   
4087          1         1         S            32       1379    2    1    1   
4088          1         1         S            33       8638    1    1    2   
4089          1         1         S            33       8638    1    1    2   
4090          1         1         S            33       8638    1    1    2   

      IV4  IV5  IV6  IV7  IV8  IV9  IV10  IV11  IV12_1  IV12_2  IV12_3  II1  \
0       2    1    1    2    1    1     1     2       2       2       2    9   
1       2    1    1    2    1    1     1     2       2       2       2    9   
2       2    1    1    2    1    1     1     2       2       2       2    9   
3       2    1    1    2    1    1     1     2       2       2       2    9   
4       3    1    1    1    1    1     1     1       2       2       2    9   
...   ...  ...  ...  ...  ...  ...   ...   ...     ...     ...     ...  ...   
4086    9    1    1    1    1    1     1     1       2       2       2    1   
4087    4    1    1    1    1    1     1     1       2       2       2    1   
4088    4    2    2    1    2    0     0     0       2       2       2    1   
4089    4    2    2    1    2    0     0     0       2       2       2    1   
4090    4    2    2    1    2    0     0     0       2       2       2    1   

      II2  II3  II3_1  II4_1  II4_2  II4_3  II5  II5_1  II6  II6_1  II7  II8  \
0       3    1      1      1      1      1    2      0    2      0    1    1   
1       3    1      1      1      1      1    2      0    2      0    1    1   
2       3    1      1      1      1      1    2      0    2      0    1    1   
3       3    1      1      1      1      1    2      0    2      0    1    1   
4       3    2      0      1      1      1    2      0    2      0    1    2   
...   ...  ...    ...    ...    ...    ...  ...    ...  ...    ...  ...  ...   
4086    1    2      0      2      2      2    0      0    0      0    3    1   
4087    1    2      0      2      2      2    0      0    0      0    3    1   
4088    1    2      0      2      2      2    0      0    0      0    2    2   
4089    1    2      0      2      2      2    0      0    0      0    2    2   
4090    1    2      0      2      2      2    0      0    0      0    2    2   

      II9  V1  V2  V21  V22  V3  V4  V5  V6  V7  V8  V9  V10  V11  V12  V13  \
0       1   1   2    2    2   2   2   2   2   2   2   2    2    2    2    2   
1       1   1   2    2    2   2   2   2   2   2   2   2    2    2    2    2   
2       1   1   2    2    2   2   2   2   2   2   2   2 

9. Agreguen a respondieron una columna llamada pobre que tome valor 1 si el `ITF` es menor al ingreso_necesario que necesita esa familia, y 0 en caso contrario.

In [12]:
respondieron = respondieron.assign(pobre = lambda row: (
    row["ingreso_necesario"]< row["ITF_x"]).astype(int))

10. En el TP2 calcularon los individuos bajo la linea de pobreza. Sin embargo, cuando se habla de pobreza el número más utilizado es el de la tasa de hogares bajo la linea de pobreza. Para calcularlo, utilicen una sola observación por hogar y sumen el ponderador `PONDIH` que permite expandir la muestra de la EPH al total de la población que representa. ¿Cuál es la tasa de hogares bajo la línea de pobreza para el GBA? ¿Se asemeja al que reporta el INDEC en sus informes? 

Aquí, primero generamos una nueva variable llamada pobreza que multiplica pobre con el ponderador para calcular la cantidad de pobres por hogar. Luego, la cantidad de pobres nos da 9.512.376 contra los 11,7 millones de personas que reporta la EPH.

In [13]:
respondieron = respondieron.assign(pobreza = lambda row:(
    row["pobre"]* row["PONDIH_y"]).astype(int))
print(respondieron)

                             CODUSU  ANO4_x  TRIMESTRE_x  NRO_HOGAR_x  \
0     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
1     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
2     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
3     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
4     TQRMNOSRPHLLNRCDEIJAH00651171    2021            1            1   
...                             ...     ...          ...          ...   
4086  TQRMNOURVHMNONCDEIIAD00700616    2021            1            1   
4087  TQRMNORRWHJMOPCDEIIAD00690119    2021            1            1   
4088  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4089  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4090  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   

      REALIZADA  REGION_x MAS_500_x  AGLOMERADO_x  PONDERA_x  IV1  IV2  IV3  \
0             1         1         S         

In [14]:
respondieron['pobreza'].sum()

9512376

## Parte II: Construcción de funciones

El objetivo de esta parte del trabajo es generar código que sea flexible y que esté modularizado (en funciones bien documentadas con docstrings). De esta forma evitarán repetir código y podrán utilizarlo en distintos escenarios (como por ejemplo la Parte III de este TP y sus proyectos personales a futuro 

1. Escriban una función, llamada `evalua_metodo`, que reciba como argumentos un modelo y los datos de entrenamiento y prueba `(X_train, y_train, X_test, y_test)`. La función debe ajustar el modelo con los datos de entrenamiento y calcular las métricas que considere necesarias para esta problemática (de mínima debe reportar la matriz de confusión, las curvas ROC y los valores de AUC y de accuracy score de cada método). El output de la función debe ser una colección con las métricas evaluadas. 

In [15]:
model_list = [LinearDiscriminantAnalysis, KNeighborsClassifier, LogisticRegression, DecisionTreeClassifier, RandomForestClassifier,
               AdaBoostClassifier, BaggingClassifier, LinearSVC]

#Para log reg models
log_reg_type = {
    "ELASTIC": {"penalty":"elasticnet","solver":"saga", "l1_ratio":0.5},
    "LASSO": {"penalty":"l1", "solver":"saga"}, 
    "RIDGE": {"penalty":"l2", "solver":"lbfgs"}, 
    
    }

#Llenar esto de configs a probar
# {parameter, range}
testingparams = {LinearDiscriminantAnalysis : ["n_components", (1,2)], 
                LogisticRegression: ["C", (1,11)], 
                KNeighborsClassifier: ["n_neighbors", (1,11)],
                DecisionTreeClassifier: ["max_features", (1,8)],
                RandomForestClassifier: ["n_estimators", (95,105)],
                AdaBoostClassifier: ["n_estimators", (47,52)],
                BaggingClassifier: ["n_estimators", (7,12)],
                LinearSVC: ["max_iter", (1000,1050)]
    }

In [16]:
def evalua_metodo(model, X_train, y_train, X_test, y_test):
    """Fitea un modelo dado a la data que se le brinda.
    Args:
        model: [Modelo a fitear]
        X_train: [Datos de entrenamiento para las variables independientes]
        y_train: [Datos de entrenamiento para las variables dependientes]
        X_test: [Datos de testeo para las variables independientes]
        y_test: [Datos de testeo para las variables dependientes]

    Returns:
        Dict: [Un diccionario con las siguientes entradas: Accuracy, ECM, Matriz de Confusión, AUC y curva ROC. ]
    """
    # Fiteamos el
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)

    # Metricas
    ecm = mean_squared_error(y_pred, y_test)
    matriz_confusion = confusion_matrix(y_test, y_pred)
    accuracy = accuracy_score(y_test, y_pred)

    auc = roc_auc_score(y_test, y_pred)
    roc_curve_data = roc_curve(y_test, y_pred)

    return {"accuracy": accuracy, "ecm": ecm, "matriz_confusion": matriz_confusion, "auc": auc, "roc_curve_data": roc_curve_data}
    

2. Escriban una función, llamada `cross_validation`, que realice validación cruzada con `k` iteraciones (k-fold CV), llamando a la función del inciso anterior en cada una, pero para las `k` distintas particiones. La función debe recibir como argumentos el modelo, el valor de `k` y un dataset (es decir, sólo `X` e `y`). Pueden ayudarse con la función KFold para generar las particiones necesarias. 

In [43]:
def cross_validation(model, X, y, k=10):
    """    Esta función realiza una validación cruzada de forma iterada para los resultados
    de la función evalua_metodo
    

    Args:
        model: [Modelo a iterar]
        X: [Datos de las variables independientes]
        y: [Datos de las variables dependientes]
        k: [Iteraciones]. Defaults to 10.

    Returns:
        [Dataframe]: [Dataframe con metricas de todas las iteraciones]
    """


    kf = KFold(n_splits=k, shuffle=True, random_state=100)
    partition, accuracy, ecm, matriz_confusion, auc, roc_curve_data = ([] for i in range(6))
    
    for i, (train_index, test_index) in enumerate(kf.split(X)):
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]
        
        metrics = evalua_metodo(model, X_train, y_train, X_test, y_test)
        
        partition.append(int(i))
        accuracy.append(metrics["accuracy"])
        ecm.append(metrics["ecm"])
        matriz_confusion.append(metrics["matriz_confusion"])
        auc.append(metrics["auc"])
        roc_curve_data.append(metrics["roc_curve_data"])
        

    return pd.DataFrame({"partition":partition,
                         "accuracy":accuracy,
                         "ecm":ecm,
                         "matriz_confusion":matriz_confusion,
                         "auc":auc,
                         "roc_curve_data":roc_curve_data})


3. Escriban una función, llamada `evalua_config` que reciba una lista de configuraciones de hiperparámetros (los distintos valores a probar como hiperparámetros podrian codificarse en diccionarios de Python) y utilizando la función `cross_validation` obtenga el error promedio para cada configuración. Finalmente, la función debe devolver la configuración que genere menor error

In [40]:
def evalua_config(X, y, model, testing_key_word, param_list_to_test, extraparams={}):
    """ Evalúa distintas configuraciones para los modelos, de forma tal de lograr obtener el menor error promedio. 

    Args:
        X : [Datos de las variables independientes]
        y : [Datos de las variables dependientes]
        model: [Modelo a evaluar]
        param_list_to_test: [Parámetros a testear]. 
        extraparams: [Otros parámetros no testeados]. Defaults to None.

    Returns:
        list: [description]
    """
   
    def get_mean_error(df, meassure="accuracy"):
        """Recupera la media del accuracy score de un dataframe determinado, que cuente con dicha medida. 

        Args:
            df ([Dataframe]): Dataframes que surgen de la función cross_validation.
            meassure (str): Datos para calcular la media. Defaults to "accuracy".
        
        Returns:
            Valor: [Media de accuracy score para el dataframe seleccionado]
        """
        return np.mean(df[meassure])
    
    list_error_dfs = [cross_validation(model(**{testing_key_word: p}, **extraparams), X, y, k=10)
                      for p in param_list_to_test]
        
    mean_accuracy_list = [get_mean_error(df) for df in list_error_dfs]    
    index_of_min_error = mean_accuracy_list.index(max(mean_accuracy_list))  
         
    return param_list_to_test[index_of_min_error], list_error_dfs[index_of_min_error]

4. Escriban una función, llamada `evalua_multiples_metodos` que les permita implementar los siguientes métodos con los hiperparámetros que ustedes elijan. Para la regresión logística, asegúrense de que esta función utilice su función `evalua_config` para optimizar el λ de la regularización. Finalmente, el output de la función debe ser una tabla donde las columnas sean las métricas que hayan evaluado (las que hayan incluido en la función `evalua_metodo`) y las filas sean los modelos (con su configuración de hiperparámetros asociada) que hayan corrido. Asegúrense de que la tabla incluya una columna con nombre del modelo y el valor de los hiperparámetros/configuración:

- Regresión logística
- Análisis de discriminante lineal
- KNN
- Arbol de decisión
- Support vector machines (SVM)
- Bagging
- Random Forests
- Boosting

In [41]:
def evalua_multiples_metodos(X, y, model_list):
   """Una función que devuelve para cada modelo, la mejor configuración dados los resultados de evaluar_config y
        cross_validation y el error promedio mínimo.  

    Args:
        X: [Datos de las variables independientes]
        y: [Datos de las variables dependientes]
        model_list: [Lista de modelos]
    Returns:
        Valor: [Media de accuracy score para el dataframe seleccionado]
    """
   
   evalua_df =  pd.DataFrame(columns=["partition", "accuracy", "ecm", 
                                      "matriz_confusion", "auc", "roc_curve_data",
                                      "Configuración", "Modelo"])

   for model in tqdm(model_list):
      testing_key_word = testingparams[model][0]  # {Parámetros} [corresponde al objeto modelo]
      min_test, max_test = testingparams[model][1] # Rangos [corresponde al objeto rangos]
      if model==LogisticRegression: # Como hay tres casos para LogisticRegression, se hace un if
         for penalty_type in log_reg_type:
            extraparams = log_reg_type[penalty_type]
            params_to_test = [i for i in range(min_test, max_test )]
            min_parameter, df_error= evalua_config(X, y, model, 
                                                      testing_key_word = testing_key_word,
                                                      param_list_to_test=params_to_test, 
                                                      extraparams = extraparams)
            config = f"{testing_key_word} = {min_parameter}, {penalty_type}"
            df_error["Configuración"] = config
            df_error["Modelo"] = model.__name__
            evalua_df = pd.concat([evalua_df, df_error], ignore_index=True)
      else:
         params_to_test = [i for i in range(min_test, max_test )] 
         min_parameter, df_error = evalua_config(X, y, model, 
                                                   testing_key_word = testing_key_word,
                                                   param_list_to_test=params_to_test)
         config = f"{testing_key_word} = {min_parameter}"
         
         df_error["Configuración"] = config
         df_error["Modelo"] = model.__name__
      
         evalua_df = pd.concat([evalua_df, df_error], ignore_index=True)
   
   evalua_df = evalua_df
   
   return evalua_df.loc[evalua_df.groupby(["Modelo", "Configuración"])['accuracy'].idxmax()].reset_index()

In [20]:
# Testeamos las funciones con un dataset de clasificaciòn binaria

from sklearn import datasets

cancer = datasets.load_breast_cancer()
X = cancer.data
y = cancer.target
df_test=evalua_multiples_metodos(X, y, model_list)
df_test

  0%|          | 0/8 [00:00<?, ?it/s]

index partition  accuracy       ecm    matriz_confusion       auc  \
0     74         4  1.000000  0.000000  [[20, 0], [0, 37]]  1.000000   
1     81         1  0.982456  0.017544  [[27, 0], [1, 29]]  0.983333   
2     51         1  0.982456  0.017544  [[26, 1], [0, 30]]  0.981481   
3     10         0  0.964912  0.035088  [[22, 0], [2, 33]]  0.971429   
4      4         4  1.000000  0.000000  [[20, 0], [0, 37]]  1.000000   
5     91         1  0.982456  0.017544  [[26, 1], [0, 30]]  0.981481   
6     21         1  0.964912  0.035088  [[25, 2], [0, 30]]  0.962963   
7     31         1  0.964912  0.035088  [[25, 2], [0, 30]]  0.962963   
8     41         1  0.982456  0.017544  [[26, 1], [0, 30]]  0.981481   
9     61         1  1.000000  0.000000  [[27, 0], [0, 30]]  1.000000   

                                      roc_curve_data       Configuración  \
0      ([0.0, 0.0, 1.0], [0.0, 1.0, 1.0], [2, 1, 0])   n_estimators = 49   
1  ([0.0, 0.0, 1.0], [0.0, 0.9666666666666667, 1....    n_estimators = 7   
2  ([0.0, 0.037037037037037035, 1.0], [0.0, 1.0, ...    max_features = 2   
3  ([0.0, 0.0, 1.0], [0.0, 0.9428571428571428, 1....    n_neighbors = 10   
4      ([0.0, 0.0, 1.0], [0.0, 1.0, 1.0], [2, 1, 0])    n_components = 1   
5  ([0.0, 0.037037037037037035, 1.0], [0.0, 1.0, ...     max_iter = 1030   
6  ([0.0, 0.07407407407407407, 1.0], [0.0, 1.0, 1...      C = 2, ELASTIC   
7  ([0.0, 0.07407407407407407, 1.0], [0.0, 1.0, 1...        C = 3, LASSO   
8  ([0.0, 0.037037037037037035, 1.0], [0.0, 1.0, ...        C = 5, RIDGE   
9      ([0.0, 0.0, 1.0], [0.0, 1.0, 1.0], [2, 1, 0])  n_estimators = 100   

                       Modelo  
0          AdaBoostClassifier  
1           BaggingClassifier  
2      DecisionTreeClassifier  
3        KNeighborsClassifier  
4  LinearDiscriminantAnalysis  
5                   LinearSVC  
6          LogisticRegression  
7          LogisticRegression  
8          LogisticRegression  
9      RandomForestClassifier

In [ ]:
def display_roc_curve(model_name, roc_curve_data, roc_auc):
    """[summary]

    Args:
        model_name ([type]): [description]
        roc_curve_data ([type]): [description]
        roc_auc ([type]): [description]
    """
    fpr, tpr, thresholds = roc_curve_data
    display = RocCurveDisplay(fpr=fpr, tpr=tpr, roc_auc=roc_auc, estimator_name = model_name)
    display.plot()
    plt.plot([0, 1], [0, 1], color='red', linestyle='--')
    plt.show()
    

display_roc_curve(df_test.iloc[0]['Modelo'], df_test.iloc[0]['roc_curve_data'], df_test.iloc[0]['auc'])

## Parte III: Clasificación y Regularización
El objetivo de esta parte del trabajo es nuevamente intentar predecir si una persona es o no pobre utilizando datos distintos al ingreso, dado que muchos hogares son reacios a responder cuánto ganan. Esta vez lo haremos con la base unida de las preguntas de la encuesta de hogar y la encuesta individual. A su vez, incluiremos ejercicios de regularización y de validación cruzada

1. Eliminen de ambas bases (`respondieron`, `norespondieron`) todas las variables relacionadas a ingresos (en el archivo `codigos_eph.pdf` ver las categorías: ingresos de la ocupación principal de los asalariados, ingresos de la ocupación principal, ingresos de otras ocupaciones, ingreso total individual, ingresos no laborales, ingreso total familiar, ingreso per cápita familiar). Elimine también las columnas adulto_equiv, ad_equiv_hogar e ingreso_necesario. Establezca a pobre como su variable dependiente (vector y). El resto de las variables serán las variables independientes (matriz X). Dependiendo de la función que usen, no se olviden de agregar la columna de 1 cuando sea necesario.


In [21]:
# Creamos dos nuevos dataframes (uno por base) donde eliminamos las columnas con valores relacionados a
# ingresos y los ponderadores asociados.
respondieronII = respondieron
norespondieronII = norespondieron

respondieronII.drop(['ITF_x'], axis='columns', inplace=True)
respondieronII.drop(['ITF_y', 'DECIFR_y', 'ADECIFR_y', 'RDECIFR_y',
                    'PDECIFR_y', 'GDECIFR_y', 'IPCF_y'], axis='columns', inplace=True)
respondieronII.drop(['P21', 'PONDIIO', 'TOT_P12', 'P47T', 'PONDII', 'V2_M', 'V3_M'],
                    axis='columns', inplace=True)
respondieronII.drop(['V4_M', 'V5_M', 'V8_M', 'V9_M', 'V10_M',
                    'V11_M'], axis='columns', inplace=True)
respondieronII.drop(['V12_M', 'V18_M', 'V19_AM', 'V21_M',
                    'T_VI', 'IPCF_x'], axis='columns', inplace=True)
# Luego eliminamos las variables en escalas decílicas
respondieronII.drop(['DECINDR', 'ADECINDR','GDECINDR', 'DECOCUR', 'ADECOCUR', 'RDECOCUR'],
                    axis='columns', inplace=True)
respondieronII.drop(['GDECOCUR', 'DECIFR_x', 'ADECIFR_x', 'RDECIFR_x', 'GDECIFR_x'],
                    axis='columns', inplace=True)
respondieronII.drop(['DECCFR_x', 'ADECCFR_x', 'RDECCFR_x', 'GDECCFR_x', 'RDECINDR'],
                    axis='columns', inplace=True)
respondieronII.drop(['IDECIFR_y', 'DECCFR_y', 'ADECCFR_y', 'RDECCFR_y', 'PDECCFR_y', 'GDECCFR_y', 'IDECCFR_y'],
                    axis='columns', inplace=True)
# Finalmente elimianamos las columnas generadas en el Punto I.
respondieronII.drop(['Adulto_equiv', 'ad_equiv_hogar',
                    'ingreso_necesario'], axis='columns', inplace=True)
# Repetimos para la segunda base
norespondieronII.drop(['ITF_x'],
                      axis='columns', inplace=True)
norespondieronII.drop(['ITF_y', 'DECIFR_y', 'ADECIFR_y', 'RDECIFR_y',
                      'PDECIFR_y', 'GDECIFR_y', 'IPCF_y'], axis='columns', inplace=True)
norespondieronII.drop(['P21', 'PONDIIO', 'TOT_P12', 'P47T', 'PONDII', 'V2_M', 'V3_M'],
                      axis='columns', inplace=True)
norespondieronII.drop(['V4_M', 'V5_M', 'V8_M', 'V9_M',
                      'V10_M', 'V11_M'], axis='columns', inplace=True)
norespondieronII.drop(['V12_M', 'V18_M', 'V19_AM', 'V21_M',
                      'T_VI', 'IPCF_x'], axis='columns', inplace=True)
# Luego eliminamos las variables en escalas decílicas
norespondieronII.drop(['DECINDR', 'ADECINDR', 'GDECINDR', 'DECOCUR', 'ADECOCUR', 'RDECOCUR'],
                      axis='columns', inplace=True)
norespondieronII.drop(['GDECOCUR', 'DECIFR_x', 'ADECIFR_x', 'RDECIFR_x', 'GDECIFR_x'],
                      axis='columns', inplace=True)
norespondieronII.drop(['DECCFR_x', 'ADECCFR_x', 'RDECCFR_x', 'GDECCFR_x', 'RDECINDR'],
                      axis='columns', inplace=True)
norespondieronII.drop(['IDECIFR_y', 'DECCFR_y', 'ADECCFR_y', 'RDECCFR_y', 'PDECCFR_y', 'GDECCFR_y', 'IDECCFR_y'],
                      axis='columns', inplace=True)
# Finalmente elimianamos las columnas generadas en el Punto I.
norespondieronII.drop(['Adulto_equiv', 'ad_equiv_hogar'], axis='columns', inplace=True)

In [22]:
print(respondieronII)

                             CODUSU  ANO4_x  TRIMESTRE_x  NRO_HOGAR_x  \
0     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
1     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
2     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
3     TQRMNOQXUHJMMUCDEIJAH00693031    2021            1            1   
4     TQRMNOSRPHLLNRCDEIJAH00651171    2021            1            1   
...                             ...     ...          ...          ...   
4086  TQRMNOURVHMNONCDEIIAD00700616    2021            1            1   
4087  TQRMNORRWHJMOPCDEIIAD00690119    2021            1            1   
4088  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4089  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   
4090  TQRMNOQWRHLOMPCDEIJAH00650932    2021            1            1   

      REALIZADA  REGION_x MAS_500_x  AGLOMERADO_x  PONDERA_x  IV1  IV2  IV3  \
0             1         1         S         

In [23]:
respondieronII.drop(['CODUSU', 'ANO4_x',
                    'ANO4_y','CH05','CH14','PP08D4'], axis='columns', inplace=True)
respondieronII.drop(['MAS_500_x'], axis='columns', inplace=True)
respondieronII.drop(['MAS_500_y'], axis='columns', inplace=True)
respondieronII.drop(['V1', 'V2', 'V21', 'V22', 'V3', 'V4', 'V5','V6','V7'],
                    axis='columns', inplace=True)
respondieronII.drop(['V8', 'V9', 'V10', 'V11', 'V12', 'V13', 'V14','V15','V16'],
                    axis='columns', inplace=True)
respondieronII.drop(['V17', 'V18', 'V19_A', 'V19_B',],
                    axis='columns', inplace=True)
respondieronII

TRIMESTRE_x  NRO_HOGAR_x  REALIZADA  REGION_x  AGLOMERADO_x  PONDERA_x  \
0               1            1          1         1            33       3255   
1               1            1          1         1            33       3255   
2               1            1          1         1            33       3255   
3               1            1          1         1            33       3255   
4               1            1          1         1            33       2331   
...           ...          ...        ...       ...           ...        ...   
4086            1            1          1         1            32       3772   
4087            1            1          1         1            32       1379   
4088            1            1          1         1            33       8638   
4089            1            1          1         1            33       8638   
4090            1            1          1         1            33       8638   

      IV1  IV2  IV3  IV4  IV5  IV6  IV7  IV8  IV9  IV10  IV11  IV12_1  IV12_2  \
0       1    9    1    2    1    1    2    1    1     1     2       2       2   
1       1    9    1    2    1    1    2    1    1     1     2       2       2   
2       1    9    1    2    1    1    2    1    1     1     2       2       2   
3       1    9    1    2    1    1    2    1    1     1     2       2       2   
4       1    9    1    3    1    1    1    1    1     1     1       2       2   
...   ...  ...  ...  ...  ...  ...  ...  ...  ...   ...   ...     ...     ...   
4086    2    1    1    9    1    1    1    1    1     1     1       2       2   
4087    2    1    1    4    1    1    1    1    1     1     1       2       2   
4088    1    1    2    4    2    2    1    2    0     0     0       2       2   
4089    1    1    2    4    2    2    1    2    0     0     0       2       2   
4090    1    1    2    4    2    2    1    2    0     0     0       2       2   

      IV12_3  II1  II2  II3  II3_1  II4_1  II4_2  II4_3  II5  II5_1  II6  \
0          2    9    3    1      1      1      1      1    2      0    2   
1          2    9    3    1      1      1      1      1    2      0    2   
2          2    9    3    1      1      1      1      1    2      0    2   
3          2    9    3    1      1      1      1      1    2      0    2   
4          2    9    3    2      0      1      1      1    2      0    2   
...      ...  ...  ...  ...    ...    ...    ...    ...  ...    ...  ...   
4086       2    1    1    2      0      2      2      2    0      0    0   
4087       2    1    1    2      0      2      2      2    0      0    0   
4088       2    1    1    2      0      2      2      2    0      0    0   
4089       2    1    1    2      0      2      2      2    0      0    0   
4090       2    1    1    2      0      2      2      2    0      0    0   

      II6_1  II7  II8  II9  IX_TOT  IX_MEN10  IX_MAYEQ10  PONDIH_x  VII1_1  \
0         0    1    1    1       4         0           4      5286       2   
1         0    1    1    1       4         0           4      5286       2   
2         0    1    1    1       4         0           4      5286       2   
3         0    1    1    1       4         0           4      5286       2   
4         0    1    2    1       4         0           4      3953       2   
...     ...  ...  ...  ...     ...       ...         ...       ...     ...   
4086      0    3    1    1       1         0           1      4325       1   
4087      0    3    1    1       1         0           1      1861      96   
4088      0    2    2    4       3         1           2     11528       1   
4089      0    2    2    4       3         1           2     11528       1   
4090      0    2    2    4       3         1           2     11528       1   

      VII1_2  VII2_1  VII2_2  VII2_3  VII2_4  TRIMESTRE_y  NRO_HOGAR_y  \
0          0      98       0       0       0            1            1   
1          0      98       0       0       0            1            1   


In [24]:
y = respondieron.pobre
X = respondieron.drop("pobre", axis=1)

2. Corran la función `multiples_metodos` con la base respondieron. En los próximos incisos profundizaremos en la tarea de regularización, pero en este ejercicio prueben al menos un hiperparámetro para regularizar y al menos un valor de λ. 

In [44]:
punto_2=evalua_multiples_metodos(X,y,model_list)
punto_2

  0%|          | 0/8 [00:00<?, ?it/s]

KeyError: "None of [Int64Index([   0,    1,    2,    3,    4,    5,    6,    7,    8,    9,\n            ...\n            2518, 2520, 2521, 2522, 2524, 2525, 2526, 2527, 2528, 2529],\n           dtype='int64', length=2277)] are in the [columns]"

3. Expliquen cómo elegiría λ por validación cruzada. Detallen por qué no usarían el conjunto de prueba (test) para su elección

Para estimar el parámetro óptimo que penaliza la complejidad del modelo se itera a partir de distintas particiones. Luego, se observa bajo que valor del parámetro el modelo ajusta mejor según el promedio de la medida de precisión elegida (EMC, accuracy score, etc.).
En validación cruzada, al partir la muestra en distintas particiones, el conjunto de testeo no se utiliza, ya que es el que se utiliza para contrastar la precisión del modelo estimado a partir del conjunto de entrenamiento. De todas formas, cuando se itera, por ejemplo, con la función K-Fold, las particiones que antes se utilizaban como entrenamiento pasan luego a utilizarse al menos una vez como conjunto de testeo.

4. En validación cruzada, ¿cuál es el problema de usar un K muy pequeño y uno muy grande? y cuando K = n (con n el número de muestras), ¿cuántas veces se estima el modelo?

Un K muy grande implica un problema de Overfit. Si bien K aumenta la complejidad y tiende el sesgo a cero,
dado que el sesgo del modelo deja de reducirse luego de un K lo suficientemente alto y que la varianza no
cesa de aumentar, el modelo comienza a perder validez externa. Por otro lado, si K=n y n es el número de 
muestras, el modelo se estimará Kxn veces para el error de pronóstico y una sola vez para los coeficientes.

5. Realicen un barrido en λ = $10^n$ con n ∈ {−5, −4, −3..., +4, +5} y utilicen 10-fold CV para elegir el λ óptimo en regresión logística con Ridge y con LASSO. ¿Qué λ seleccionó en cada caso? Generen box-plots mostrando la distribución del error de predicción para cada λ. Cada box debe corresponder a un valor de λ y contener como observaciones el error medio de validación para cada partición. Además, para la regularización LASSO, genere un box-plot similar, pero ahora graficando la proporción de variables ignoradas por el modelo en función de λ, es decir la proporción de variables para las cuales el coeficiente asociado es cero. 

In [26]:
respondieronII.drop(['pobreza'], axis='columns', inplace=True)


In [27]:
alphas = 10**np.linspace(-5,5)
alphas

array([1.00000000e-05, 1.59985872e-05, 2.55954792e-05, 4.09491506e-05,
       6.55128557e-05, 1.04811313e-04, 1.67683294e-04, 2.68269580e-04,
       4.29193426e-04, 6.86648845e-04, 1.09854114e-03, 1.75751062e-03,
       2.81176870e-03, 4.49843267e-03, 7.19685673e-03, 1.15139540e-02,
       1.84206997e-02, 2.94705170e-02, 4.71486636e-02, 7.54312006e-02,
       1.20679264e-01, 1.93069773e-01, 3.08884360e-01, 4.94171336e-01,
       7.90604321e-01, 1.26485522e+00, 2.02358965e+00, 3.23745754e+00,
       5.17947468e+00, 8.28642773e+00, 1.32571137e+01, 2.12095089e+01,
       3.39322177e+01, 5.42867544e+01, 8.68511374e+01, 1.38949549e+02,
       2.22299648e+02, 3.55648031e+02, 5.68986603e+02, 9.10298178e+02,
       1.45634848e+03, 2.32995181e+03, 3.72759372e+03, 5.96362332e+03,
       9.54095476e+03, 1.52641797e+04, 2.44205309e+04, 3.90693994e+04,
       6.25055193e+04, 1.00000000e+05])

In [30]:
y = respondieronII.pobre
X = respondieronII.drop("pobre", axis=1)

In [33]:
from sklearn.preprocessing import scale
from sklearn.linear_model import Lasso, LassoCV, Ridge, RidgeCV

In [37]:
lasso = Lasso(max_iter=10000, normalize=True)
coefs = []

for a in alphas:
    lasso.set_params(alpha=a)
    lasso.fit(X, y)
    coefs.append(lasso.coef_)
    
np.shape(coefs)

(50, 79)

In [38]:
X_train, X_test , y_train, y_test = train_test_split(X, y, test_size=0.5, random_state=1)
lassocv = LassoCV(alphas= alphas, cv=10, max_iter=100000, normalize=True)
lassocv.fit(X_train, y_train)
lasso.set_params(alpha=lassocv.alpha_)
print("Alpha=", lassocv.alpha_)
lasso.fit(X_train, y_train)
print("mse = ",mean_squared_error(y_test, lasso.predict(X_test)))
print("Mejores coeficientes:")
pd.Series(lasso.coef_, index=X.columns)
pd.set_option('display.max_rows', None) 
display(pd.Series(lasso.coef_, index=X.columns))

Alpha= 0.0006866488450042998
mse =  0.16148945726518435
Mejores coeficientes:


TRIMESTRE_x     0.000000
NRO_HOGAR_x    -0.000789
REALIZADA       0.000000
REGION_x        0.000000
AGLOMERADO_x   -0.044625
PONDERA_x      -0.000011
IV1            -0.000000
IV2             0.000000
IV3            -0.063165
IV4             0.003268
IV5            -0.020802
IV6            -0.000000
IV7            -0.000000
IV8             0.000000
IV9            -0.000000
IV10           -0.115974
IV11           -0.000000
IV12_1          0.000000
IV12_2          0.007556
IV12_3          0.000000
II1             0.024512
II2             0.000000
II3             0.000000
II3_1          -0.000000
II4_1          -0.000000
II4_2          -0.002165
II4_3          -0.000000
II5             0.056101
II5_1           0.000000
II6             0.000000
II6_1           0.000000
II7            -0.002563
II8            -0.124024
II9            -0.000000
IX_TOT         -0.050714
IX_MEN10       -0.015590
IX_MAYEQ10     -0.000000
PONDIH_x        0.000000
VII1_1          0.000222
VII1_2          0.000000


In [32]:
ridgecv = RidgeCV(alphas=alphas, cv=10, normalize=True)
ridgecv.fit(X_train, y_train)
print("Alpha=", ridgecv.alpha_)
ridge = Ridge(alpha=ridgecv.alpha_, normalize=True)
ridge.fit(X_train, y_train)
print("mse = ",mean_squared_error(y_test, ridge.predict(X_test)))
print("best model coefficients:")
pd.Series(ridge.coef_, index=X.columns)

Alpha= 2.0235896477251556
mse =  0.16060390394921237
best model coefficients:


TRIMESTRE_x     0.000000e+00
NRO_HOGAR_x    -5.424359e-03
REALIZADA       0.000000e+00
REGION_x        0.000000e+00
AGLOMERADO_x   -3.340408e-02
                    ...     
PP02C8         -1.648252e-02
PP02E           4.892096e-03
PP02H          -3.961834e-03
PP02I          -4.517955e-03
PONDIH_y       -7.836139e-08
Length: 79, dtype: float64

6. En el caso del valor óptimo de λ para LASSO encontrado en el inciso anterior,¿qué variables fueron descartadas? ¿Son las que hubieran esperado? ¿Tienerelación con lo que respondió en el inciso 1 de la Parte I?

Las principales variables a las que Lasso no les dio prioridad fueron: TRIMESTRE_x, REALIZADA, REGION_x, IV1, IV2, IV6, IV7, IV8, IV9, IV11, IV12_1, IV12_3, II2, II3, II3_1, II4_1, II4_3, II5_1, II6, II6_1, II9, IX_MAYEQ10, PONDIH_x, VII1_2, VII2_1, VII2_2, VII2_4, TRIMESTRE_y, NRO_HOGAR_y, COMPONENTE, H15, REGION_y, PONDERA_y, CH03, CH04, CH07, CH09, CH10, CH11, CH12, CH13, CH15, CH16, ESTADO, CAT_OCUP, PP02C1, PP02C3, PP02C4, PP02C5, PP02C6, PP02C8, PP02E, PP02H, PP02I, PONDIH_y.
No hubieramos esperado que de aquellas que caracterizan a los miembros del hogar haya tan pocas. No obstante, como se mencionó en el punto 1.1, efectivamente las variables de vivienda no terminan siendo buenos regresores para la clasificación.

    

7. Elijan alguno de los modelos de regresión logistica donde haya probado distintos parametros de regularización y comente: ¿Qué metodo de regularización funcionó mejor Ridge o LASSO? Comente mencionando el error cuadrático medio (ECM). 

In [ ]:
El método de regularización que mejor funcionó cuando utilizamos el evaluador de múltiples métodos en el punto 2 fue el
estimador ridge. Su error cuadrático medio fue de 0.017544 contra el 0.035088 que arrojó el Lasso.

8. Cuál de todos los métodos evaluados predice mejor? ¿Con qué hiperparámetros? Justifiquen detalladamente utilizando las medidas de precisión que conoce.

EL método que mejor predice dentro del Linear regression es el Ridge. Esto lo podemos ver ya que tiene el menor error tipo 2, la mayor precisión y el mayor AUC, Los hiperparámetros son C=5, lo que indica la inversa de lambda.

9. Con el método que seleccionó, predigan qué personas son pobres dentro de la base norespondieron. ¿Qué proporción de los hogares son pobres en esa submuestra? 

In [45]:
norespondieronII.drop(['CODUSU', 'ANO4_x',
                    'ANO4_y','CH05','CH14','PP08D4'], axis='columns', inplace=True)
norespondieronII.drop(['MAS_500_x'], axis='columns', inplace=True)
norespondieronII.drop(['MAS_500_y'], axis='columns', inplace=True)
norespondieronII.drop(['V1', 'V2', 'V21', 'V22', 'V3', 'V4', 'V5','V6','V7'],
                    axis='columns', inplace=True)
norespondieronII.drop(['V8', 'V9', 'V10', 'V11', 'V12', 'V13', 'V14','V15','V16'],
                    axis='columns', inplace=True)
norespondieronII.drop(['V17', 'V18', 'V19_A', 'V19_B',],
                    axis='columns', inplace=True)
norespondieronII

TRIMESTRE_x  NRO_HOGAR_x  REALIZADA  REGION_x  AGLOMERADO_x  PONDERA_x  \
18              1            1          1         1            32       4300   
19              1            1          1         1            32       4300   
20              1            1          1         1            32       4300   
21              1            1          1         1            32       4300   
22              1            1          1         1            32       4300   
23              1            1          1         1            32       4300   
24              1            1          1         1            32       4300   
25              1            1          1         1            32       4300   
30              1            1          1         1            32       3090   
31              1            1          1         1            32       3090   
32              1            1          1         1            32       3090   
33              1            1          1         1            32       3090   
34              1            1          1         1            32       3090   
42              1            1          1         1            33       3852   
43              1            1          1         1            33       3852   
52              1            1          1         1            32       3118   
53              1            1          1         1            32       3118   
54              1            1          1         1            32       3118   
55              1            1          1         1            32        258   
56              1            1          1         1            32        258   
57              1            1          1         1            32        258   
58              1            1          1         1            32        258   
59              1            1          1         1            32        258   
72              1            1          1         1            33       3703   
73              1            1          1         1            33       3703   
74              1            1          1         1            33       3703   
75              1            1          1         1            33       3703   
76              1            1          1         1            33        363   
77              1            1          1         1            33        363   
83              1            1          1         1            33       1324   
84              1            1          1         1            33       1324   
85              1            1          1         1            33       1324   
86              1            1          1         1            33       1324   
87              1            1          1         1            33       1324   
88              1            1          1         1            33       1324   
96              1            1          1         1            33       1626   
97              1            1          1         1            33       1626   
98              1            1          1         1            33       1626   
99              1            1          1         1            33        331   
100             1            1          1         1            33        331   
101             1            1          1         1            33        331   
102             1            1          1         1            33        331   
103             1            1          1         1            33       1991   
104             1            1          1         1            33       1991   
105             1            1          1         1            33       6337   
106             1            1          1         1            33       6337   
107             1            1          1         1            33       6337   
116             1            1          1         1            33       1051   
117             1            1          1         1            33       1051   
118   

In [46]:
x_nr=norespondieron

In [50]:
x_nr_train, x_nr_test,= train_test_split(X, test_size=0.5, random_state=1)
ridge = Ridge(alpha = 1.2648552168552958 , normalize = True)
ridge.fit(X_train, y_train)             
y_pred_nr = ridge.predict(x_nr_test)
y_pred_nr
pobres = (y_pred_nr).sum()
pobres

840.2869194023635

NameError: name 'y_pred_nr' is not defined